# DFC foracst
### Author: Karozis Stelios
### Date: 12/4/2021
### Source: https://codingandfun.com/discounted-cash-flow-with-python-valuing-a-company/

## Libs import

In [743]:
import requests
import numpy as np
import pandas as pd
import pandas_datareader.data as web
import datetime
import plotly.graph_objects as go
pd.options.display.float_format = '{:,.2f}'.format

## User inputs

In [684]:
y_ahead=5
date_start = [2019,3,1]
timeframe=0 #analysis for current year: 0, analysis for previous year: 1 etc
company = 'GOOG' #'VWS.DE' #VESTAS
demo = '34c9e7a6a6fcfb7b1d531f1267eac987'

In [652]:
IS = requests.get('https://financialmodelingprep.com/api/v3/income-statement/'+company+'?apikey='+demo).json()

In [653]:
BS = requests.get('https://financialmodelingprep.com/api/v3/balance-sheet-statement/'+company+'?apikey='+demo).json()

In [654]:
FR = requests.get('https://financialmodelingprep.com/api/v3/ratios/'+company+'?apikey='+demo).json()

In [655]:
profile = requests.get('https://financialmodelingprep.com/api/v3/company/profile/'+company+'?apikey='+demo).json()

In [729]:
historical_prices = requests.get('https://financialmodelingprep.com/api/v3/historical-price-full/'+company+'?apikey='+demo).json()

In [741]:
history = requests.get('https://financialmodelingprep.com/api/v3/historical-price-full/'+company+'?apikey='+demo).json()

## FCF forecast

#### Functions

In [594]:
def income_perc_years_ahead(IS,timeframe, y_ahead, revenue_g):
    #Get net income
    #net_income = dataframe[0]['netIncome']
    #get income statement as % of revenue for future predictions and forecast 5 next IS years
    income_statement = pd.DataFrame.from_dict(IS[timeframe],orient='index')


    #income_statement = income_statement[6:27]
    income_statement.columns = ['current_year']
    income_statement['as_ratio_of_revenue'] =  np.nan
    for i in income_statement.index:
        try:
            #print(type(income_statement['current_year'][i]), income_statement['current_year'][i], type(net_income),net_income)
            income_statement['as_ratio_of_revenue'][i] = float(income_statement['current_year'][i]) / float(income_statement['current_year']['revenue'])
        except:
            pass
  
    
    for y in range(1,y_ahead+1):
        if y==1:
            cl_nm='next'+str(y)+'year'
            prev='current_year'
        else:
            cl_nm='next'+str(y)+'year'
            prev='next'+str(y-1)+'year'
        #print(cl_nm)
        income_statement[cl_nm] =  np.nan
        #for i in income_statement.index:
        income_statement[cl_nm] = (income_statement[prev]['revenue'] * (1+revenue_g)) \
                                    * income_statement['as_ratio_of_revenue'] 
                                   
    return income_statement

In [568]:
def balance_perc_years_ahead(BS, timeframe, income_statement, y_ahead):
    #Get Balance sheet as a percentage of revenue
    balance_sheet = pd.DataFrame.from_dict(BS[timeframe],orient='index')
    balance_sheet.columns = ['current_year']
    balance_sheet['as_ratio_of_revenue'] =  np.nan
    for i in balance_sheet.index:
        try:
            balance_sheet['as_ratio_of_revenue'][i] = float(balance_sheet['current_year'][i]) \
                                                / float(income_statement['current_year']['revenue'])
        except:
            pass
        
    for y in range(1,y_ahead+1):
        cl_nm='next'+str(y)+'year'
        #print(cl_nm)
        balance_sheet[cl_nm] = income_statement[cl_nm]['revenue']  \
                                    * balance_sheet['as_ratio_of_revenue'] 
       
    return balance_sheet

In [602]:
def CF_forecast_perc_years_ahead(income_statement, balance_sheet, y_ahead):
    CF_forecast = {}
    
    for y in range(1,y_ahead+1):
        if y==1:
            cl_nm='next'+str(y)+'year'
            prev='current_year'
        else:
            cl_nm='next'+str(y)+'year'
            prev='next'+str(y-1)+'year'
        #print(cl_nm)
        CF_forecast[cl_nm] = {}
        CF_forecast[cl_nm]['netIncome'] = income_statement[cl_nm]['netIncome']
        CF_forecast[cl_nm]['inc_depreciation'] = income_statement[cl_nm]['depreciationAndAmortization'] - income_statement[prev]['depreciationAndAmortization']
        CF_forecast[cl_nm]['inc_receivables'] = balance_sheet[cl_nm]['netReceivables'] - balance_sheet[prev]['netReceivables']
        CF_forecast[cl_nm]['inc_inventory'] = balance_sheet[cl_nm]['inventory'] - balance_sheet[prev]['inventory']
        CF_forecast[cl_nm]['inc_payables'] = balance_sheet[cl_nm]['accountPayables'] - balance_sheet[prev]['accountPayables']
        CF_forecast[cl_nm]['CF_operations'] = CF_forecast[cl_nm]['netIncome'] + CF_forecast[cl_nm]['inc_depreciation'] + (CF_forecast[cl_nm]['inc_receivables'] * -1) + (CF_forecast[cl_nm]['inc_inventory'] *-1) + CF_forecast[cl_nm]['inc_payables']
        CF_forecast[cl_nm]['CAPEX'] = balance_sheet[cl_nm]['propertyPlantEquipmentNet'] - balance_sheet[prev]['propertyPlantEquipmentNet'] + income_statement[cl_nm]['depreciationAndAmortization']

        CF_forecast[cl_nm]['FCF'] = CF_forecast[cl_nm]['CAPEX'] + CF_forecast[cl_nm]['CF_operations']
        
        #add the forecasted cash flows into a Pandas
        CF_forec = pd.DataFrame.from_dict(CF_forecast,orient='columns')

        #add below option to format the dataframe with thousand separators
        #pd.options.display.float_format = '{:,.2f}'.format
       
    return CF_forec

In [740]:
def historical_prices(history):

    historical_prices = history['historical']
    price_data = {}

    for item in historical_prices:
        price_data[item['date']] = {}
        price_data[item['date']]['date'] = item['date']
        price_data[item['date']]['open']= item['open']
        price_data[item['date']]['high'] = item['high']
        price_data[item['date']]['low'] = item['low']
        price_data[item['date']]['adjClose'] = item['adjClose']

    price_DF = pd.DataFrame.from_dict(price_data)
    price_DF = price_DF.T	
    fig = go.Figure(data=[go.Candlestick(x=price_DF['date'],
                open=price_DF['open'],
                high=price_DF['high'],
                low=price_DF['low'],
                close=price_DF['adjClose'])])

    fig.show()

#### Calculations

In [744]:
historical_prices(history)

In [690]:
count = 0
#get revenue growth to estimate future sales
revenue_g = []
for item in IS:
    if count < 4:
        #print(item)
        revenue_g.append(item['revenue'])
        count = count + 1
for i in range(len(revenue_g)-1):
    print(i,(revenue_g[i] - revenue_g[i+1]) /revenue_g[i+1])

revenue_g = (revenue_g[timeframe] - revenue_g[timeframe+1]) /revenue_g[timeframe+1] 
print('Revenue variation of the last year:',round(revenue_g*100,2),'%')

0 0.12770532012826136
1 0.1830008989979462
2 0.23421586757475982
Revenue variation of the last year: 12.77 %


In [691]:
income_statement = income_perc_years_ahead(IS,timeframe, y_ahead, revenue_g)

/share/apps/gnu/8.2.0/soft/python-3.5.7/lib/python3.5/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [692]:
balance_sheet=balance_perc_years_ahead(BS,timeframe, income_statement, y_ahead)

/share/apps/gnu/8.2.0/soft/python-3.5.7/lib/python3.5/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':


In [598]:
#balance_sheet
#income_statement

In [693]:
CF_forecast = CF_forecast_perc_years_ahead(income_statement, balance_sheet, y_ahead)
CF_forecast

next1year         next2year         next3year  \
CAPEX            27,828,487,609.43 31,382,333,528.28 35,390,024,477.88   
CF_operations    43,773,617,100.28 49,363,740,885.24 55,667,753,217.72   
FCF              71,602,104,709.71 80,746,074,413.52 91,057,777,695.60   
inc_depreciation  1,749,179,769.80  1,972,559,332.26  2,224,465,653.26   
inc_inventory        92,969,473.05    104,842,169.37    118,231,072.17   
inc_payables        713,745,034.20    804,894,072.28    907,683,327.45   
inc_receivables   4,007,903,766.91  4,519,734,400.50  5,096,928,529.01   
netIncome        45,411,565,536.24 51,210,864,050.58 57,750,763,838.20   

                          next4year          next5year  
CAPEX             39,909,518,883.18  45,006,176,768.32  
CF_operations     62,776,821,463.21  70,793,755,544.81  
FCF              102,686,340,346.39 115,799,932,313.12  
inc_depreciation   2,508,541,751.62   2,828,895,879.07  
inc_inventory        133,329,809.10     150,356,735.05  
inc_payables       1,023,599,317.36   1,154,318,395.86  
inc_receivables    5,747,833,418.48   6,481,862,325.23  
netIncome         65,125,843,621.81  73,442,760,330.16

## WACC

#### Functions

In [576]:
#Interest coverage ratio = EBIT / interest expenses

def interest_coverage_and_RF(IS,timeframe, st_date=[]):
    EBIT= IS[timeframe]['ebitda'] - IS[timeframe]['depreciationAndAmortization'] 
    interest_expense = IS[timeframe]['interestExpense']
    interest_coverage_ratio = EBIT / interest_expense

    #RF
    start = datetime.datetime(st_date[0], st_date[1], st_date[2])

    #end= datetime.datetime.today().strftime('%Y-%m-%d')
    end= datetime.datetime(st_date[0]+1, st_date[1], st_date[2]).strftime('%Y-%m-%d')
    
    Treasury = web.DataReader(['TB1YR'], 'fred', start, end)
    
    RF = float(Treasury.iloc[-1])
    RF = RF/100
    
    return [RF,interest_coverage_ratio]

In [577]:
#Cost of debt
def cost_of_debt(RF,interest_coverage_ratio):
    if interest_coverage_ratio > 8.5:
        #Rating is AAA
        credit_spread = 0.0063
    if (interest_coverage_ratio > 6.5) & (interest_coverage_ratio <= 8.5):
        #Rating is AA
        credit_spread = 0.0078
    if (interest_coverage_ratio > 5.5) & (interest_coverage_ratio <=  6.5):
        #Rating is A+
        credit_spread = 0.0098
    if (interest_coverage_ratio > 4.25) & (interest_coverage_ratio <=  5.49):
        #Rating is A
        credit_spread = 0.0108
    if (interest_coverage_ratio > 3) & (interest_coverage_ratio <=  4.25):
        #Rating is A-
        credit_spread = 0.0122
    if (interest_coverage_ratio > 2.5) & (interest_coverage_ratio <=  3):
        #Rating is BBB
        credit_spread = 0.0156
    if (interest_coverage_ratio > 2.25) & (interest_coverage_ratio <=  2.5):
        #Rating is BB+
        credit_spread = 0.02
    if (interest_coverage_ratio > 2) & (interest_coverage_ratio <=  2.25):
        #Rating is BB
        credit_spread = 0.0240
    if (interest_coverage_ratio > 1.75) & (interest_coverage_ratio <=  2):
        #Rating is B+
        credit_spread = 0.0351
    if (interest_coverage_ratio > 1.5) & (interest_coverage_ratio <=  1.75):
        #Rating is B
        credit_spread = 0.0421
    if (interest_coverage_ratio > 1.25) & (interest_coverage_ratio <=  1.5):
        #Rating is B-
        credit_spread = 0.0515
    if (interest_coverage_ratio > 0.8) & (interest_coverage_ratio <=  1.25):
        #Rating is CCC
        credit_spread = 0.0820
    if (interest_coverage_ratio > 0.65) & (interest_coverage_ratio <=  0.8):
        #Rating is CC
        credit_spread = 0.0864
    if (interest_coverage_ratio > 0.2) & (interest_coverage_ratio <=  0.65):
        #Rating is C
        credit_spread = 0.1134
    if interest_coverage_ratio <=  0.2:
        #Rating is D
        credit_spread = 0.1512

    cost_of_debt = RF + credit_spread
    
    return cost_of_debt

In [615]:
def costofequity(company, profile, RF, st_date=[]):


  #Start end dates
    start = datetime.datetime(st_date[0], st_date[1], st_date[2])
    #end= datetime.datetime.today().strftime('%Y-%m-%d')
    end= datetime.datetime(st_date[0]+1, st_date[1], st_date[2]).strftime('%Y-%m-%d')

#Beta

    beta = float(profile['profile']['beta'])
    stock_cur = float(profile['profile']['price'])

  #Market Return
    SP500 = web.DataReader(['sp500'], 'fred', start, end)
      #Drop all Not a number values using drop method.
    SP500.dropna(inplace = True)

    SP500yearlyreturn = (SP500['sp500'].iloc[-1]/ SP500['sp500'].iloc[-252])-1
    
    cost_of_equity = RF+(beta*(SP500yearlyreturn - RF))
    
    return cost_of_equity, stock_cur

In [613]:
#effective tax rate and capital structure
def wacc(company, BS, FR, timeframe, ke, kd):

    ETR = FR[timeframe]['effectiveTaxRate']

# 
    Debt_to = BS[timeframe]['totalDebt'] / (BS[timeframe]['totalDebt'] + BS[timeframe]['totalStockholdersEquity'])
    equity_to = BS[timeframe]['totalStockholdersEquity'] / (BS[timeframe]['totalDebt'] + BS[timeframe]['totalStockholdersEquity'])

    WACC = (kd*(1-ETR)*Debt_to) + (ke*equity_to)
    
    return WACC

#### Calculations

In [694]:
RF_and_IntCov = interest_coverage_and_RF(IS,timeframe, st_date=date_start) 
RF = RF_and_IntCov[0]
interest_coverage_ratio = RF_and_IntCov[1]
ke, stock_cur = costofequity(company, profile, RF, st_date=date_start)
kd = cost_of_debt(RF,interest_coverage_ratio)
wacc_company = wacc(company, BS, FR, timeframe, ke, kd)
print('wacc of ' + company + ' is ' + str((wacc_company*100))+'%')

wacc of GOOG is 4.980497654294513%


## Net Present Value of the Forecasted Free Cash Flows

In [695]:
#FCF List of CFs for each year
FCF_List = CF_forecast.loc[['FCF']].values[0].tolist()
npv = np.npv(wacc_company,FCF_List)

## Terminal Value

The net present value obtained in the section F covers only the next 5 years of the company cash flows. But what happen after these forecasted years?

We need to calculate the terminal value of the company. The terminal value captures the value of the company after the forecasting period. The terminal value will constitute at least 50% of the forecasted value. Therefore, it is super important to pay attention to the assumptions that we make here. 

We will assume 2% perpetuity rate since it is a common practice to be in line with the long-term inflation rate which is usually around 2%. Then, we discount the value using the WACC rate.

In [696]:
#Terminal value
LTGrowth = 0.02

Terminal_value = (CF_forecast['next'+str(y_ahead)+'year']['FCF'] * (1+ LTGrowth)) /(wacc_company  - LTGrowth)

Terminal_value_Discounted = Terminal_value/(1+wacc_company)**4
#Terminal_value_Discounted

## Target Price

In [697]:
target_equity_value = Terminal_value_Discounted + npv
debt = balance_sheet['current_year']['totalDebt']
target_value = target_equity_value - debt
numbre_of_shares = requests.get('https://financialmodelingprep.com/api/v3/enterprise-values/'+company+'?apikey='+demo).json()
numbre_of_shares = numbre_of_shares[0]['numberOfShares']

target_price_per_share = target_value/numbre_of_shares
#target_price_per_share

In [698]:
print(company + ' current price per stock is ' + str(stock_cur) )
print(company + ' forecasted price per stock is ' + str(target_price_per_share) )
print('The forecast is based on the following assumptions:')
print('     Revenue growth:    ',round(revenue_g*100,2),'%')
print('     Cost of Capital:   ', round(wacc_company*100,2),'%' )
print('     Perpetuity growth: ', round(LTGrowth*100,2),'%')

GOOG current price per stock is 2300.01
GOOG forecasted price per stock is 5272.227316237697
The forecast is based on the following assumptions:
     Revenue growth:     12.77 %
     Cost of Capital:    4.98 %
     Perpetuity growth:  2.0 %
